<h1> Week 2 Assignment </h1>

<h2> Introduction </h2>

Opening a restaurant is the easiest way to make money. On the contrary, it is way more complicated. So how complicated? There are many factors one has to consider before opening a restaurant. One deciding factor is location. Why location? A luxury restaurant in a poor village, a beef-specialized restaurant in Hindus community are all examples of poor choice of location. How to choose a good location? Worst news is that there is no correct answer like in maths. We have to use try-and-error method to figure out which works well and which doesn't. Changing restaurant's location several time really hurts one's pocket. It is a costly process. A process which can be greatly reduced in cost if we utilize Data Science.

This task provides suggestions of place for those looking to open a restaurant.

<h2> Data </h2>

The data is taken from Now.vn, a food delivery company in Viet Nam. It features following criteria:

1. Restaurant Name

2. Address

3. Website

4. Kind of Restaurant

5. Number of Approached People

6. Price Range

7. Food Category

8. Food Item

9. Food Cost

10. Latitude

11. Longitude

In which, our problem will mostly need and use these criteria: 

* Group 1: Identify Suitable Location

1. Address: to cluster area where restaurants have a high number of approached people

2. Number of Approached People: to measure number of approached people

3. Latitude, Longitude: to learn the location of restaurant

* Group 2: Identify Restaurant 's Characteristics which are suitable for a given area

3. Kind of Restaurant: to understand what kind of restaurant most famous in a given area

4. Price Range: to identify price range most attractive to local people

5. Food Category: to undestand what kind of food most attractive to local people


* Four Square restaurant will be used as test set to see whether our model gives a good suggestion:

Three criteria will be chosen: 

+ Categories: Provide information about the restaurant to be used for prediction

+ Latitude: Provide real location to test prediction

+ Longitude: Provide real location to test prediction

In [1]:
import requests
import pandas as pd
import numpy as np
import re
import json
import requests as req
import folium
from folium.plugins import HeatMap
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler
import scipy

Scrap data from Now.vn

In [ ]:
from bs4 import BeautifulSoup
import requests as req
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import ElementClickInterceptedException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import time
import re

RESTAURANT_CLASS_NAME = 'name-res'
RESTAURANT_CLASS_LOCATION = 'address-res'
RESTAURANT_KIND = 'kind-restaurant'
HOW_MANY_PEOPLE = 'number-rating'
COST_RANGE = 'cost-restaurant'
CATEGORY = 'item' #list, Lấy list item bỏ giá trị đầu
FOODS_ITEM = 'item-restaurant-name' #list
FOODS_COST = 'current-price' #list
CLASS_NAME_DETAILS = {0:RESTAURANT_KIND,1:HOW_MANY_PEOPLE,2:COST_RANGE,3:CATEGORY,4:FOODS_ITEM,5:FOODS_COST}
CLASS_NAME = {0:RESTAURANT_CLASS_NAME, 1:RESTAURANT_CLASS_LOCATION}

def change_page(driver = None, targeted_page = None, start_page = None, jump_step = 1, time_needed = 8):
    old_ele = None
    while start_page < targeted_page:
        ele = None
        start_page += min(jump_step,targeted_page-start_page)
        while ele == None:
            time.sleep(time_needed)
            try:
                print('change_page: Currently at page {}'.format(start_page))
                print('change_page: Real current = {}'.format(driver.find_element_by_class_name('undefined').text))
                ele = driver.find_element_by_link_text(str(start_page))
            except NoSuchElementException:
                print('change_page: cannot find element')

        while driver.find_element_by_class_name('undefined').text != str(start_page):
            print('change_page: force click {}'.format(start_page))
            try:
                ele.click()
            except ElementClickInterceptedException:
                print('change_page: cannot click')
            time.sleep(time_needed)

    return driver

def initialize_driver():
    chrome_options = Options()
    chrome_options.add_argument('--headless')
    driver = webdriver.Chrome(options = chrome_options, keep_alive=True)
    #driver = webdriver.Chrome()

    return driver

def get_summary(restaurant_infos, driver=None):
    finish_load = False 
    progress_counter = 0
    while finish_load == False:
        print('get_summary: checkpoint_1')
        time.sleep(2)
        for index in range(progress_counter,len(CLASS_NAME)):
            div = driver.find_elements_by_class_name(CLASS_NAME[index])
            #check if div has not fully loaded
            if len(div) == 0:
                finish_load = False
                break

            finish_load = True
            if index == 0:
                for item in div:
                    restaurant_infos.append({0:item.text,1:'',2:'',3:'',4:'',5:'',6:'',7:'',8:''})
                progress_counter += 1
            else:
                counter = 0
                for item1 in div:
                    restaurant_infos[counter][index] = item1.text
                    counter+=1
                progress_counter += 1

    soup = BeautifulSoup(driver.page_source,'lxml')
    link_list = soup.find_all('a',attrs = {'class':'item-content'})
    counter = 0
    for link in link_list:
        restaurant_infos[counter][2] = 'https://www.now.vn' + link['href']
        counter+=1

    print('get_summary: checkpoint_2')

    return restaurant_infos

def get_details(restaurant_infos, item = None, driver = None): 
    print(item)
    driver.get(restaurant_infos[item][2])
    
    finish_load = False 
    progress_counter = 0
    while finish_load == False:
        print('get_details: checkpoint1 at url: {} in {}'.format(restaurant_infos[item][2],progress_counter))
        time.sleep(2)
        for index in range(progress_counter,len(CLASS_NAME_DETAILS)):
            ele_contain = driver.find_elements_by_class_name(CLASS_NAME_DETAILS[index])
            #make sure everything is loaded
            if index == 3:
                if len(ele_contain) == 0:
                    break

                ele_contain.pop(0)
                finish_load = True
            for ele_item in ele_contain:
                restaurant_infos[item][index+3] += ele_item.text + '|'
            progress_counter+=1
    
    print('get_details: checkpoint2')
    
    return restaurant_infos

def write_to_csv(restaurant_infos):
    print('Writing file')
    length = len(restaurant_infos)
    file = open('GloriousNowData.csv','a',encoding = 'utf-8',newline='\n')

    for restaurant_item in range(length):
        for i in restaurant_infos[restaurant_item-1]:
            file.write(restaurant_infos[restaurant_item-1][i])
            if i < len(restaurant_infos[0])-1:
                file.write(';')
        
        file.write('\n')
    
    file.close()

In [ ]:
url = 'https://www.now.vn/ha-noi/food/deals'
driver = initialize_driver() #driver for changing summary page
driver1 = initialize_driver() #driver for changing detail page
driver.get(url)
start_page = 51
end_page = 80
#load page until it reachs start_page_number 
driver = change_page(driver = driver, targeted_page=start_page, start_page=6, jump_step=4)

for i in range(start_page,end_page+1):
    print('page {}'.format(i))
    restaurant_infos = []
    if i > start_page:
        driver = change_page(driver = driver, targeted_page=i,start_page=i-1)
    restaurant_infos = get_summary(restaurant_infos,driver= driver)
    for restaurant_item in range(len(restaurant_infos)):
        restaurant_infos = get_details(restaurant_infos, item = restaurant_item, driver = driver1)
    write_to_csv(restaurant_infos)

driver1.close()
driver.close()

Get latitude and longitude of each restaurant

In [ ]:
driver = initialize_driver()
    
df = pd.read_csv('CleanedDataFrame.csv',sep=';',encoding='utf-8')
f = open('Location.txt','a')
start = 100
for i in range(start,len(df['WEBSITE'])):
    driver.get(df['WEBSITE'][i])
    has_element = False
    break_counter = 0
    while not has_element:
        time.sleep(8)
        result = re.search('"latitude":\d*.\d*,"longitude":\d*.\d*',driver.page_source)   
        if result == None:
            #attempts before break
            break_counter += 1
            if break_counter == 3:
                print('break at {}'.format(i))
                break
            else:
                continue
        print('result= {}'.format(result.group()))
        location = re.findall('\d+(?:.\d+)?',result.group())
        f.write('{};{}'.format(location[0],location[1]))
        f.write('\n')
        has_element = True

f.close()
driver.close()

Construct dataframe from data of Now.vn

In [2]:
df = pd.read_csv('CleanedDataFrame.csv', sep=";")
df_loc = pd.read_csv('Location.csv', sep=";")
df.head()

RESTAURANT_NAME  \
0                        Pizza Mập - Pizza Online   
1  Chè Ngon Hà Nội & Món Ngon Đường Phố - Tô Hiệu   
2              Cơm Tấm Sài Gòn Út Thắng - Tô Hiệu   
3                    Trà Sữa Kai Tea - Thanh Niên   
4            An Huy - Cơm Tấm & Bánh Canh Sài Gòn   

                                             ADDRESS  \
0              50/514 Thụy Khuê, Quận Tây Hồ, Hà Nội   
1                 297 Tô Hiệu, Quận Cầu Giấy, Hà Nội   
2  105 B8 Tô Hiệu, P. Nghĩa Tân, Quận Cầu Giấy, H...   
3                  9 Thanh Niên, Quận Tây Hồ, Hà Nội   
4              114 Chiến Thắng, Quận Hà Đông, Hà Nội   

                                             WEBSITE          RESTAURANT_KIND  \
0   https://www.now.vn/ha-noi/pizza-map-pizza-online              SHOP ONLINE   
1          https://www.now.vn/ha-noi/che-ngon-ha-noi            ĂN VẶT/VỈA HÈ   
2         https://www.now.vn/ha-noi/com-tam-ut-thang       QUÁN ĂN -Chi nhánh   
3  https://www.now.vn/ha-noi/tra-sua-kai-tea-than...  CAFÉ/DESSERT -Chi nhánh   
4  https://www.now.vn/ha-noi/an-huy-com-tam-banh-...                  QUÁN ĂN   

   NUMBER_OF_APPROACHED_PEOPLE     PRICE_RANGE  \
0                        100.0  70000 - 130000   
1                        500.0   15000 - 20000   
2                        999.0   30000 - 70000   
3                        500.0   20000 - 60000   
4                        100.0   35000 - 50000   

                                            CATEGORY  \
0                       PIZZA|MỲ SPAGHETTI|NƯỚC UỐNG   
1  CHÈ NGON BỐN MÙA|SỮA CHUA|HOA QUẢ|NƯỚC ÉP HOA ...   
2                MÓN CHÍNH|MÓN CANH|MÓN THÊM|ĐỒ UỐNG   
3  FRESH MILK TEA|TROPICAL FRUIT TEA|CHEESE TEA|B...   
4                                       MENU|ĐỒ THÊM   

                                           FOOD_ITEM  \
0  Pizza Bò Hầm Đặc Biệt|Pizza Hải Sản|Combo 1.|P...   
1  Chè Thập Cẩm|Chè Khúc Bạch Trà Xanh, Nhãn|Chè ...   
2  Cơm Sườn Cốt Lết|Cơm Đùi Gà Nướng Tỏi|Cơm Sườn...   
3  Matcha Nhật Bản Sữa Tươi|Sữa tươi trân châu đư...   
4  Cơm Sườn|Cơm Sườn Bì Chả Trứng Đặc Biệt|Cơm Sư...   

                                           FOOD_COST  
0  97750|102000|170000|102000|136000|97750|59500|...  
1  20900|23750|20900|26600|23750|23750|23750|2090...  
2  36000|40500|58500|49500|40500|31500|49500|4050...  
3  27300|30800|27300|27300|25200|27300|27300|2730...  
4  40500|56700|46150|46150|46150|40500|40500|4050...

Size of our data set

In [3]:
df.shape

(1897, 9)

Get Longitude and Latitude of Restaurant

In [4]:
df_loc = pd.read_csv('Location.csv',sep=';')
df_loc.head()

Latitude   Longitude
0  21.050153  105.810217
1  21.041525  105.790895
2  21.042209  105.795261
3  21.043523  105.836258
4  20.980313  105.795320

Data Cleaning

In [105]:
df.loc[:,'Latitude'] = df_loc.loc[:,'Latitude']
df.loc[:,'Longitude'] = df_loc.loc[:,'Longitude']
df = df.astype({'Latitude':'float','Longitude':'float','NUMBER_OF_APPROACHED_PEOPLE':'str','RESTAURANT_KIND':'str'})
df.dtypes

RESTAURANT_NAME                 object
ADDRESS                         object
WEBSITE                         object
RESTAURANT_KIND                 object
NUMBER_OF_APPROACHED_PEOPLE     object
PRICE_RANGE                     object
CATEGORY                        object
FOOD_ITEM                       object
FOOD_COST                       object
Latitude                       float64
Longitude                      float64
dtype: object

Clean FOOD_COST

In [106]:
na_table = df['FOOD_COST'].isna()
print(na_table.value_counts(dropna=False))

False    1890
True        7
Name: FOOD_COST, dtype: int64


In [107]:
cr_df = df[~na_table]
cr_df.reset_index()
print(len(cost_related_table))

1890


Clean RESTAURANT_KIND

In [108]:
#exclude 'QUÁN ĂN'
regex_content = "(CAFÉ/DESSERT)|(SHOP ONLINE)|(ĂN VẶT/VỈA HÈ)|(TIỆM BÁNH)|(ĂN CHAY)|(SHOP/CỬA HÀNG)|(QUÁN NHẬU)|(NHÀ HÀNG)|(QUÁN ĂN)"
for index,value in df['RESTAURANT_KIND'].items():
    res = re.search(regex_content,str(value))
    if not res == None:
        df.loc[index,'RESTAURANT_KIND'] = res.group()

In [109]:
df['RESTAURANT_KIND'].value_counts(dropna=False)

CAFÉ/DESSERT     600
QUÁN ĂN          503
SHOP ONLINE      300
ĂN VẶT/VỈA HÈ    287
NHÀ HÀNG         108
nan               58
TIỆM BÁNH         32
ĂN CHAY            4
SHOP/CỬA HÀNG      3
QUÁN NHẬU          2
Name: RESTAURANT_KIND, dtype: int64

Get data from Four Square as test set

In [20]:
secret = dict(
    v=20200323,
    client_id='H0IZ23LNW3Y4DDUGZEPW4SBIVS2QCQE0SKLAMP15UZMQGPPU',
    client_secret='IUSOYUQKPVUKYOYYP4OV1WB1BPOJ4IGI0R0JBS4UPDPEIYFS',
    ll='21.028511,105.804817',
    categoryId='4d4b7105d754a06374d81259',
    limit = 50
)

secret_detail = dict(
    v=20200323,
    client_id='H0IZ23LNW3Y4DDUGZEPW4SBIVS2QCQE0SKLAMP15UZMQGPPU',
    client_secret='IUSOYUQKPVUKYOYYP4OV1WB1BPOJ4IGI0R0JBS4UPDPEIYFS'
)

In [21]:
url = 'https://api.foursquare.com/v2/venues/search'

resp = requests.get(url=url, params=secret)
data = json.loads(resp.text)

Save to a file

In [8]:
data_body = data['response']['venues']
f = open('FourSquareData.csv','a',encoding='utf-8')
for i in range(len(data_body)):
    if i == 0:
        continue
    
    url = 'https://api.foursquare.com/v2/venues/{}'.format(data_body[i]['id'])
    det_res = req.get(url=url, params = secret_detail)
    data_res = json.loads(det_res.text)

    #Save Categories
    body = data_res['response']['venue']
    length = len(body['categories'])
    for cat_i in range(length):
        f.write('{}-{}'.format(body['categories'][cat_i]['id'],body['categories'][cat_i]['name']))
        if not cat_i == length-1: 
            f.write('|')

    f.write(';')
    #Save Location
    f.write('{};{}\n'.format(body['location']['lat'],body['location']['lng']))

f.close()

"\ndata_body = data['response']['venues']\nf = open('FourSquareData.csv','a',encoding='utf-8')\nfor i in range(len(data_body)):\n    if i == 0:\n        continue\n    \n    url = 'https://api.foursquare.com/v2/venues/{}'.format(data_body[i]['id'])\n    det_res = req.get(url=url, params = secret_detail)\n    data_res = json.loads(det_res.text)\n\n    #Save Categories\n    body = data_res['response']['venue']\n    length = len(body['categories'])\n    for cat_i in range(length):\n        f.write('{}-{}'.format(body['categories'][cat_i]['id'],body['categories'][cat_i]['name']))\n        if not cat_i == length-1: \n            f.write('|')\n\n    f.write(';')\n    #Save Location\n    f.write('{};{}\n'.format(body['location']['lat'],body['location']['lng']))\n\nf.close()\n"

Construct dataframe from Four Square data

In [6]:
fs_df = pd.read_csv('FourSquareData.csv',sep=';')
fs_df.head()

Categories   Latitude   Longitude
0  4bf58dd8d48988d11c941735-Sake Bar|4bf58dd8d489...  21.035236  105.809476
1  4bf58dd8d48988d1d1941735-Noodle House|4bf58dd8...  21.034373  105.854382
2               4bf58dd8d48988d1e0931735-Coffee Shop  21.022716  105.852515
3  4bf58dd8d48988d1e0931735-Coffee Shop|4bf58dd8d...  21.029162  105.850222
4               4bf58dd8d48988d1e0931735-Coffee Shop  21.010801  105.849220

First construct map to give firm understanding

In [7]:
hanoi_map = folium.Map(location=[21.028511,105.804817],zoom_start=12)

#add a bunch of markers to hanoi map
loc = df[['Latitude','Longitude']]

for i in range(loc.shape[0]):
    location = [loc.loc[i,'Latitude'],loc.loc[i,'Longitude']]
    folium.Circle(radius=16,location=location).add_to(hanoi_map)

hanoi_map

Map about approached people

In [118]:
approached_people = df['NUMBER_OF_APPROACHED_PEOPLE']
print(approached_people.value_counts(dropna=False))
print(approached_people.unique())

color_hex=dict({'red':'#ff0000','orange':'#ffa500','yellow':'#ffff00','green':'#008000','blue':'#0000ff','indigo':'#4b0082','violet':'#ee82ee'})
#Loai color 1
#Nan là đỏ
#dưới mười là Cam
#Mỗi giá trị mà trên mười là một màu khác nhau
colors = dict({'nan':color_hex['red'],'5.0':color_hex['orange'],'6.0':color_hex['orange'],'7.0':color_hex['orange'],'8.0':color_hex['orange'],'9.0':color_hex['orange'],'10.0':color_hex['orange'],'50.0':color_hex['yellow'],'100.0':color_hex['green'],'500.0':color_hex['blue'],'999.0':color_hex['indigo']})

#Loại color 2
#Nan là đỏ
#dưới 50 là Cam
#trên 50 là Xanh
colors_2 = dict({'nan':color_hex['red'],'5.0':color_hex['blue'],'6.0':color_hex['blue'],'7.0':color_hex['blue'],'8.0':color_hex['blue'],'9.0':color_hex['blue'],'10.0':color_hex['blue'],'50.0':color_hex['orange'],'100.0':color_hex['orange'],'500.0':color_hex['orange'],'999.0':color_hex['orange']})

100.0    565
999.0    399
10.0     253
500.0    235
50.0     192
nan      184
6.0       18
8.0       14
9.0       13
5.0       13
7.0       11
Name: NUMBER_OF_APPROACHED_PEOPLE, dtype: int64
['100.0' '500.0' '999.0' '50.0' '10.0' 'nan' '6.0' '9.0' '8.0' '5.0' '7.0']


In [119]:
hanoi_map = folium.Map(location=[21.028511,105.804817],zoom_start=12)

for i in range(loc.shape[0]):
    location = [loc.loc[i,'Latitude'],loc.loc[i,'Longitude']]
    folium.Circle(radius=9,color=colors_2[approached_people.iloc[i]],location=location,fill_color=colors_2[approached_people.iloc[i]],fill_opacity=1.0).add_to(hanoi_map)

hanoi_map

Here is the map of about 2000 restaurants in Hanoi. Orange circle indicates restaurant with more than 100 reviews. Blue circle indicates restaurant with number of reviews ranging from 5 to more than 50 reviews. As you can see, there are some areas with remarkedly high number of orange circles. Places such as new - development zones or old imperial city district have a hugh number of circles. However, some places which are also new - development zones don't record many restaurants. I will further gain insights about this map to have a clearer understanding.

identify price range for each region

In [116]:
def vectorize_method_easy_median(x):
    x = np.round(x/10000)*10000
    return x

def identify_price_tag(kind):
    kind_df = cr_df[cr_df['RESTAURANT_KIND'] == kind]
    p_list = []
    length = kind_df.shape[0]

    for index in kind_df['FOOD_COST']:
        temp = list(map(lambda x: int(x) if x != '' else None,index.split('|')))
        temp.pop()
        temp = list(map(int,np.vectorize(vectorize_method_easy_median)(temp)))
        mode = scipy.stats.mode(temp)
        p_list.append(mode[0])
    
    expansive_threshold = scipy.stats.mode(p_list)[0].astype(int)[0]
    
    pt_list = []
    for index in range(length):
        tag = 'cheap' if p_list[index] <= expansive_threshold else 'expansive'
        pt_list.append(tag)

    return pt_list,kind_df


In [117]:
hanoi_map = folium.Map(location=[21.028511,105.804817],zoom_start=12)

unique_kind = cr_df['RESTAURANT_KIND'].unique()
for kind in unique_kind:
    #identify_color
    if kind == 'nan':
        kind_df = cr_df[cr_df['RESTAURANT_KIND'] == kind]
        for i in range(len(kind_df)):
            location = [kind_df.iloc[i,9],kind_df.iloc[i,10]]
            folium.Circle(radius=9,color=color_hex['red'],location=location,fill_color=color_hex['red'],fill_opacity=1.0).add_to(hanoi_map)
    else:
        pt_list,kind_df = identify_price_tag(kind)
        for i in range(len(kind_df)):
            location = [kind_df.iloc[i,9],kind_df.iloc[i,10]]
            color = color_hex['blue'] if pt_list[i] == 'cheap' else color_hex['orange']
            folium.Circle(radius=9,color=color,location=location,fill_color=color,fill_opacity=1.0).add_to(hanoi_map)
    
hanoi_map

<h1>Methodology</h1>

The goal is to understand which zone is most attractive to a certain types of restaurant and understand why that zone is attractive?

1. Choose a kind of restaurant which is 'CAFÉ/DESSERT' to analyze. Further explore with price range.

2. Create heatmap to focus on an area to do analyze what criteria makes it a good place

3. Cluster other areas which share same criteria

Find out which region is most attractive to 'CAFÉ/DESSERT'

In [129]:
def map_res_kind(kind,color,map):
    res_kind = df[df['RESTAURANT_KIND'] == kind]
    loc_list = list()
    f = open('cafe_location.csv','a')
    for i in res_kind.index:
        location = [res_kind.loc[i,'Latitude'],res_kind.loc[i,'Longitude']]
        loc_list.append(location)
        counter = 0
        for j in location:
            counter += 1
            f.write(str(j))
            if counter == 1:
                f.write(',')
        f.write('\n')
        folium.Circle(radius=9,color=color,location=location,fill_color=color, fill_opacity=1.0).add_to(map)

    HeatMap(loc_list, name='Cafe/Dessert', radius = 12, min_opacity=5).add_to(hanoi_map)
    return loc_list

hanoi_map = folium.Map(location=[21.028511,105.804817],zoom_start=13)
kind = 'CAFÉ/DESSERT'
loc_list = map_res_kind(kind,color_hex['orange'],hanoi_map)

hanoi_map

After some field missions, I have deduced the following criteria: 
RESTAURANT_LIMIT_PER_ZONE. 
I have found out that there are some areas which can harbor many cafe, dessert and still produce profits amidst fierce competition. There are some areas which can only sustain a small amount of cafe, dessert. 
The question to be answered is "how big a zone can be?" and "how many restaurant can a zone sustain?"

For example: In Đào Tấn street, there are an unusual high concentration of banks and offices for lease. It is also where two universities, 4 school, two embassies, a market, ... reside. The zone with a hugh flowing of pops has up to 24 cafe, dessert. My deduction is that it is both a financial zone and a zone with hugh gathering of young pops. And those 24 cafe, dessert reside right in the center of the zone. However, just 2km Northward, Đội Cấn street only has about 3, 4 cafe. It doesn't have a hugh concentration of pops.  

If the concentration of pops is the determining factor to RESTAURANT_LIMIT_PER_ZONE, then new development zone might hold the answer to where can I open a profitable cafe. However, determining the projected concentration of pops is no easy deal. Therefore, I will have to rely on other metrics to figure it out. 

"How big a zone can be?"
To answer this question, I will use DBSCAN clustering to cluster zones. Find the center of said zones and find distance from the center to neighboring zone 's centers. Find the median of all distances.  

In [130]:
def recognize_cafe_zone(loc_list,map=None,big=5):
    X = StandardScaler().fit_transform(loc_list)
    db = DBSCAN(eps=0.11, min_samples=big).fit(X)

    cluster_num = len(set(db.labels_)) - (1 if -1 in db.labels_ else 0)
    print('Estimated number of clusters: {}'.format(cluster_num))
    print('Estimated number of noises: {}'.format(list(db.labels_).count(-1)))
    labels = list(db.labels_)
    easy_color = list(color_hex.values())
    #decide which cluster get what color
    cluster_color = list()
    for i in range(cluster_num):
        cluster_color.append(easy_color[i%6])
    
    for i in range(len(loc_list)):
        chosen_color = color_hex['violet'] if labels[i] == -1  else cluster_color[labels[i]]
        folium.Circle(radius=9,color=chosen_color,location=loc_list[i],fill_color=chosen_color, fill_opacity=1.0).add_to(hanoi_map)

    return labels

hanoi_map = folium.Map(location=[21.028511,105.804817],zoom_start=13)
labels = recognize_cafe_zone(loc_list,map=hanoi_map,big=4)
hanoi_map

Estimated number of clusters: 49
Estimated number of noises: 164


In [131]:
#find center
length = len(set(labels)) - (1 if -1 in labels else 0)
center_list = [[0,0,0] for _ in range(length)]
for i in range(len(labels)):
    if not labels[i] == -1:
        center_list[labels[i]][0] += loc_list[i][0]
        center_list[labels[i]][1] += loc_list[i][1]
        center_list[labels[i]][2] += 1

for i in range(length):
    center_list[i][0] = center_list[i][0]/center_list[i][2]
    center_list[i][1] = center_list[i][1]/center_list[i][2]

#draw_circle
for lis in center_list:
    folium.Circle(radius = 22*22, location=[lis[0],lis[1]]).add_to(hanoi_map)

hanoi_map

If you look at the spot, you can see that all the circles stand closely to each others. However, in Thành Công zone, there is no cafe/dessert. Which is strange, it is the place with lakes, national cinema center, a populated area, .... Thành Công zone is supposed to be a place with many cafe, dessert I guest. And a field trip to that zone verifies my assumption. Thành Công zone has up to 20 cafe/dessert on google map and still many more. It is a robust zone for cafe/dessert.

Now knowing that my model has the predictive ability, I will proceed to identify each zone's restaurant price range.  

In [133]:
pt_list, kind_df = identify_price_tag('CAFÉ/DESSERT')
length = len(kind_df)
pts_zone = [list() for _ in range(length)]
pt_zone = ['' for _ in range(length)]

for i in range(length):
    if labels[i] != -1:
        pts_zone[labels[i]].append(pt_list[i])

for i in range(length):
    pt_zone[i] = scipy.stats.mode(pts_zone[i])[0]

for i in range(length):
    if pt_zone[i] == 'expansive':
        folium.Circle(radius = 22*22, location=[center_list[i][0],center_list[i][1]],color=color_hex['red']).add_to(hanoi_map)

hanoi_map

The red circle indicates zone which has more expansive cafe/dessert than inexpansive ones. In Viet Nam, a two dolar cup of coffe is pretty expansive, a five dolar cup of coffe is reserved only for the rich and the passionate. The area around Ba Đình has many expansive cafe/dessert. It is the center of Viet Nam capital city and a famous tourist site. The pops there are usually rich and often love to enjoy life. Further away from the center, in new development zone, it can be clearly seen that red zone doesn't show up a lot more with few exception.

<h1>Result and Discussion</h1>

<p>Ha Noi is a coffee loving city. Ha Noi is also a place where people often gather a litte bit too much to enjoy the taste of life. You can easily see a coffee store everywhere in Ha Noi with a lot of people just drinking and watching the bustling street. Basically, you can open a coffee house anywhere in Ha Noi and still earn a respectable income. However, it also leads to fierce competition that drive many, who thought it would be easy, out of business. A decent coffee cup and a good place can earn you a lot. A good place is what this project intends to find.</p>
<br>
<p>The analysis shows a dense concentration of cafe in every corner of Ha Noi with exception of a few province. By using DBSCAN clustering to cluster all those cafes, I have been able to narrow down key zones with high concentration of coffee houses. The more closely a zone is to the center of Ha Noi, the more coffee house it can harbor. Lakes are famous for opening a cofe. Universities are famous for opening store that serves sweet drinks like Taiwanese Tea. In summary, it is RESTAURANT_LIMIT_PER_ZONE. Lakes can attract people to come and enjoy the taste of life which is very much loved by Ha Noi citizen. Universities are full of youngsters who have a lot of free time playing around. Indeed that RESTAURANT_LIMIT_PER_ZONE is greatly affected by surrounding sites, there is still exception to this that I have not yet understood</p>
<br>
<p>Well, a little bit off - topic, the majority of Ha Noi citizen are really lazy. They are more on enjoying life. </p>

<h1>Conclusion</h1>

The goal is to find the most suitable place to open a restaurant. To ease the process in this project, I choose cafe as this project main target. By clustering all coffee/dessert houses in Ha Noi, I have been able to identify deciding criteria, what attracts people to a cafe. As well as learning about some potential area that can open cafe. 